# AI-powered Brochure Generator
---
- Task: Generate a company brochure using its name and website for clients, investors, and recruits.
- Model: Toggle `USE_OPENAI` to switch between OpenAI and Ollama models
- Data Extraction: Scraping website content and filtering key links (About, Products, Careers, Contact).
- Output Format: a Markdown-formatted brochure streamed in real-time.
- Tools: BeautifulSoup, OpenAI API, and IPython display, ollama.
- Skill Level: Intermediate.

🛠️ Requirements
- ⚙️ Hardware: ✅ CPU is sufficient — no GPU required
- 🔑 OpenAI API Key 
- Install Ollama and pull llama3.2:3b or another lightweight model
---
📢 Find more LLM notebooks on my [GitHub repository](https://github.com/shivachaudhary46/LLM_Engineering)

![](Workflow.png)

# Importing Necessary Libraries

In [1]:
from openai import OpenAI
import ollama 
import os
import json
import requests
from IPython.display import display, Markdown, update_display
from bs4 import BeautifulSoup
from dotenv import load_dotenv

# Here I use ollama qwen3 as my goto model 
because i don't have the gpt4o model api. I have loaded an api_key from the .env file which is also known as secret file. In .env file secrets key are stored and make sure to ignore the file while pushing in GitHub because you don't want any person to use your hard paid api keys. If api_key doesn't startswith('sk-') raise the ValueError saying invalid OpenAI API key. I have use llama3.1 but you can use deepseek-r1, gemma3, qwen3 or any model you like from Ollama. You can use Hugging face inference model as well. 

In [8]:
# load api key 
# load_dotenv()
# api_key = os.getenv('OPENAI_API_KEY')
# if not api_key or not api_key.startswith('sk-'):
#     raise ValueError("Invalid OpenAI API Key. Check your .env file")

use_ollama = True # True if we are using ollama and False to use OpenAI
model = "llama3.1" if use_ollama else 'gpt-4o'

# openai_client = OpenAI() if use_openai else None

# since we don't have paid version of api of gpt-4o 
# so i will be commenting this code if you want to use it 
# you can do that. 

# In Class Structure Website
- extract_texts() methods which remove irrelevant things from the response. here' response means getting an requests and extracting all the elements from that url. 

- another extract_links() methods which scrape only links from that website. 

- get_content() method compile all the relevant contents from that url website. 

In [3]:
headers = {
        "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/117.0.0.0 Safari/537.36"
    }

class website:

    def __init__(self, url):
        self.url = url
        response = requests.get(url, headers=headers)
        soup = BeautifulSoup(response.content, 'html.parser')
        self.title = soup.title.string if soup.title else "No Title Found"
        self.text = self.extract_texts(soup)
        self.link = self.extract_links(soup)

    def extract_texts(self, soup):
        if soup.body:
            for irrelevant in soup.body(['img', "input", "script", "style"]):
                irrelevant.decompose()

            return soup.body.get_text(separator='\n', strip=True)
        return ""
    
    def extract_links(self, soup):
        links = [link.get('href') for link in soup.find_all('a')]
        return [link for link in links if link and ('http' in link or 'https' in link)]
    
    def get_contents(self):
        return f"website title: \n{self.title}\n and website content: \n{self.text}\n\n"

# In Class Structure Generate LLM Link 
- get_relevant_link() methods which makes an LLM call or AI call which returns totally relevant links in the json format. 

- another generate_brochure() method takes all the relevant links, process it and makes AI call and start generating funny, Jokey Brochure.  


In [6]:
class generate_LLM_link:

    def __init__(self, model=model):
        self.model = model

    def get_relevant_link(self, website):
        link_system_prompt = """
            you will be given a list of links from a company website. 
            select only relevant links for a brochure like (About, Company, Carrers, Products)
            Exclude (login, emails, terms, and privacy) which are not needed for brochure. 

            Instructions to follow: 
            - return on valid json
            - do not include explanations, comments or markdown
            - example of output: 
            {
                "links": [
                    {"type": "about", "url": "https://company.com/about"},
                    {"type": "contact", "url": "https://company.com/contact"},
                    {"type": "product", "url": "https://company.com/products"}
                ]
            }
        """
        # links = { link for link in website.link}
        link_user_prompt = f"""
            Here is a list of the links you can find on the website of {website.url}
            please identify the relevant web links needed for company brochure. Respond in json.
            Do not include login, emails, terms and privacy.
            {website.link}. 
        """
        link_user_prompt += """
            return in json format, like this:
            {
                "links": [
                    {"type": "about", "url": "https://company.com/about"},
                    {"type": "contact", "url": "https://company.com/contact"},
                    {"type": "product", "url": "https://company.com/products"}
                ]
            }
        """
        if use_ollama:
            response = ollama.chat(
                model = model,
                messages = [
                    {"role": "system", "content": link_system_prompt},
                    {'role': "user", "content": link_user_prompt}
                ]
            )     

            result = response['message']['content'].strip()
        else:
            response = openai.chat.completions.create(
                model = self.model,
                messages=[
                    {"role": "system", "content": link_system_prompt},
                    {"role": "user", "content": user_prompt}
                ]
            )
            result = response.get("message", {}).get("content", "").strip()
        
        try :
            links = json.loads(result)
            return [link for link in links['links'] if link['url'].startswith(('https', 'http'))]
        except json.JSONDecodeError:
            print("Error: response is not valid json")
            return {"links": []} # return empty links 

    def generate_brochure(self, company_name, Language, content, website):
        system_prompt = """
            You are an assistant that analyses the contents of several relevant pages from 
            website. and you will create a humoous, entertaining, joey brochure about the company
            for customers, investors, stock holders and recruits. Respond in the markdown. 
            Include details of company culture, customers and carrer /jobs if you have the information. 
        """

        # links = {link for link in website.link}
        user_prompt = f"""
            You are looking at company called: {website.url}. 
            Here are the contents of the landing, contact, about and other rerlevant pages. 

            here's example of brochure which you can take a look: 

            🌍 Brochure for La Tour Eiffel
                🗼 Welcome to the Icon of Paris

                The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity!
                Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

                💡 Fun Facts
                - Built for the World’s Fair (and wasn’t supposed to stay forever!).
                - Weighs over 10,000 tons, but still manages to look graceful.
                - Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

                🎟️ What We Offer
                - Tickets & Tours – Skip the line (because life’s too short).
                - Restaurants – Enjoy French cuisine with a side of ooh la la views.
                - Events & Exhibitions – Because Paris is never boring.

                👩‍💻 Careers at the Tower
                - Ever dreamt of working in the heart of Paris, 300 meters up in the sky?
                We’re looking for:
                    - Hospitality heroes
                    - Engineers with nerves of steel
                    - Dreamers who want to light up the city

                📞 Contact Us
                🌐 Website: toureiffel.paris
                📍 Location: Champ de Mars, 5 Av. Anatole France, 75007 Paris
                ✨ The Eiffel Tower: not just a monument, but a love story in iron.

            Use this information to build short brochure of the company in markdown format.
            links are: 
            {website.link}

            and 
            {content}
        """

        if use_ollama:
            response_stream = ollama.chat(
                model = model, 
                messages=[
                    {"role": "system", "content": system_prompt},
                    {"role": "user", "content": user_prompt}
                ], 
                stream=True
            )

            response = ""
            display_handle = display(Markdown(""), display_id=True)
            for chunk in response_stream:
                content += chunk.get("message", {}).get("content", "")
                if content:
                    response += content.replace("```", "")
                    update_display(Markdown(response), display_id=display_handle.display_id)

            return response

In [7]:
generate_link = generate_LLM_link()
links = generate_link.get_relevant_link(a_j)
print(links)

Error: response is not valid json
{'links': []}


In [8]:
print(len([link for link in links if link['url'].startswith('https' or 'http')]))

10


In [9]:
for link in links['links']:
    print(link)

TypeError: list indices must be integers or slices, not str

# Class Structure Generate brochure
It is compilation and in this generate() method, all the relevant links contents are extracted which are again added to the final content and final content is provided for the second LLM call to create a brochure

In [11]:
class generate_brochure:

    def __init__(self, company_name, url, language="English"):
        self.company_name = company_name
        self.url = url
        self.language = language
        self.website = website(self.url)
        self.llm_client = generate_LLM_link()

    def generate(self):
        links = self.llm_client.get_relevant_link(self.website)
        content = self.website.get_contents()

        for link in links:
            linked_website = website(link['url'])
            content += f"\n\n{link['type']}:\n"
            content += linked_website.get_contents() 

        return self.llm_client.generate_brochure(self.company_name, self.language, content, linked_website)


In [15]:
url = "https://www.toureiffel.paris/en"
tower = website(url)

links = generate_LLM_link()
all_links = links.get_relevant_link(tower)
print(all_links)

Error: response is not valid json
{'links': []}


In [14]:
contents = ""

for link in all_links:
    other_link_content = website(link["url"])
    contents += f"\n{link['type']}"
    contents += f"\n{other_link_content.get_contents()}"

print(contents)

NameError: name 'all_links' is not defined

# Output

In [12]:
def main():
    company_name = "LA TOUR EIFIEL"
    url = "https://www.toureiffel.paris/en"
    language = "English"

    generator = generate_brochure(company_name, url)
    generator.generate()


if __name__ == "__main__":
    main()

website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Herewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here iswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is awebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorouswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous andwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertainingwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochurewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure aboutwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about thewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Ewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffelwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Towerwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower companywebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company inwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdownwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown formatwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Browebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochurewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure forwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for Lawebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tourwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Ewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffelwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcomewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome towebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to thewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Iconwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon ofwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Pariswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

Thewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Ewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffelwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Towerwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isnwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’twebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t justwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just anwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an ironwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiecewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece –website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – itwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’swebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s awebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a globalwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebritywebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity!website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standingwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tallwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall sincewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 188website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889,website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, shewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’swebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seenwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen morewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfieswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies thanwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than anywebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any otherwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmarkwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark inwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in thewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the worldwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Funwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Factswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

*website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Builtwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built forwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for thewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the Worldwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’swebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fairwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (andwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasnwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’twebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposedwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed towebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to staywebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay foreverwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!)website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
*website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Wewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs overwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tonswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons,website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, butwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but stillwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manageswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages towebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to lookwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look gracefulwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
*website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Haswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hostedwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinnerswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners,website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworkswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks,website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposalswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals,website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, andwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and evenwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachutewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumpswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (donwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’twebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t trywebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try thiswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this atwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at homewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ Whatwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What Wewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offerwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

*website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Ticketswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets &website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tourswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours –website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skipwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip thewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the linewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (becausewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because lifewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’swebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s toowebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too shortwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
*website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurantswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants &website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shopswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops –website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoywebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy awebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a tastewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste ofwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Pariswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
*website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenancewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance &website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operationswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations –website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keepingwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping thewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the towerwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standingwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tallwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careerswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers atwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at Lawebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tourwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Ewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffelwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

Wewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We havewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staffwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff workingwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hardwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard everywebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every daywebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day towebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to runwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run thewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Ewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffelwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Towerwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower andwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcomewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitorswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors fromwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from allwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all overwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over thewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the worldwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world.website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Ourwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employeeswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees arewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proudwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud towebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to workwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work forwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for thewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Ewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffelwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Towerwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower,website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, servingwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving itswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitorswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors,website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, andwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possesswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess anwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellentwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent teamwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spiritwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meetwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Ourwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teamswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

*website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcomewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agentswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents –website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almostwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost halfwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half ofwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of ourwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our totalwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staffwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
*website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technicalwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical departmentwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department –website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keepingwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping thewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the towerwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower runningwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothlywebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
*website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Saleswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales,website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Financewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance,website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketingwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communicwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communicationswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications,website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, ITwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT,website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legalwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal,website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, andwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Humanwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resourceswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departmentswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments –website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keepingwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping thewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the companywebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company runningwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running aswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as itwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it shouldwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Joinwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Ourwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Teamwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SEwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETEwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourageswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internalwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobilitywebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility andwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and careerwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career developmentwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development forwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for itswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staffwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff.website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. Wewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We havewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have anwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitiouswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HRwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policywebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy thatwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promoteswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes genderwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equalitywebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality andwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversitywebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contactwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Uswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Dowebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do youwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you havewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have awebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a questionwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question aboutwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about ourwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HRwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policywebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy orwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or wouldwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would youwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you likewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like towebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to applywebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneouslywebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously?website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contactwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact uswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Followwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Uswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

*website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebookwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook:website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @Ewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @Eiffwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @Eiffelwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTowerwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
*website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitterwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter:website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @Ewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @Eiffwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @Eiffelwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTowerwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
*website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagramwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram:website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @Ewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @Eiffwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @Eiffelwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTowerwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Staywebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connectedwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Getwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get thewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latestwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest newswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news andwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updateswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates fromwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from thewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Ewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffelwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Towerwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower onwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower on ourwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower on our socialwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower on our social mediawebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower on our social media channelswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower on our social media channels.

website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower on our social media channels.

Iwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower on our social media channels.

I hopewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower on our social media channels.

I hope youwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower on our social media channels.

I hope you enjoywebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower on our social media channels.

I hope you enjoy thiswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower on our social media channels.

I hope you enjoy this brochurewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower on our social media channels.

I hope you enjoy this brochure!website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower on our social media channels.

I hope you enjoy this brochure! Letwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower on our social media channels.

I hope you enjoy this brochure! Let mewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower on our social media channels.

I hope you enjoy this brochure! Let me knowwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower on our social media channels.

I hope you enjoy this brochure! Let me know ifwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower on our social media channels.

I hope you enjoy this brochure! Let me know if youwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower on our social media channels.

I hope you enjoy this brochure! Let me know if you havewebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower on our social media channels.

I hope you enjoy this brochure! Let me know if you have anywebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower on our social media channels.

I hope you enjoy this brochure! Let me know if you have any furtherwebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower on our social media channels.

I hope you enjoy this brochure! Let me know if you have any further requestswebsite title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower on our social media channels.

I hope you enjoy this brochure! Let me know if you have any further requests.website title: 
The OFFICIAL Eiffel Tower website: tickets, news, info...
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Eiffel Tower
Welcome on the Official Website
Buy a ticket
What to know today
Come and enjoy a nice break on the 1st floor of the Eiffel Tower on our green summer terrace!
The Tower's Garden
Dine on the 1st floor at Madame Brasserie: watch the Paris skyline while you have diner. Without reservation, subject to availability.
More information
Tip! Connect to our mobile visitor's guide, a real companion to find your way around and learn more about the Tower!
Try
Waiting times
Attendance:
Low
Opening times
09:30 - 23:00
Access map
Coming to the Tower
Events at the Tower
Pink October 2025
30 September 2025
View all events
Explore
A journey to the top
Come and discover the Eiffel Tower on the only trip to the top of its kind in Europe, and let pure emotions carry you from the esplanade to the top.
Discover the Eiffel Tower
Now at the Tower
Make the perfect gift
Discover unique gifts, rare authentic collectibles and official products for unforgettable moments!
Eiffel Tower Effect
Come and discover the ultimate immersive experience
Free mobile visitor's guide
Enhance your experience at the Tower with your mobile phone. No download required!
News
Giving women scientists their rightful place on the Eiffel T...
A commission of experts is studying the possibility of inscribing the names of women scientists on the Eiffel Tower.
Paris Firefighters Take Over the Eiffel Tower!
Free for all visitors – come explore the photo exhibition “Scaling the ladder”.
Précédent
Suivant
See all the news
Don't miss
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Restaurants & stores
On every floor, the Eiffel Tower has a range of dining and gift-shop options.
The Gustave Eiffel Salon
For your business events, hire a new venue in a magical setting. Fully equipped to meet all of your needs.
If you are
A family
Professional in the Tourism Industry
A business
Teachers
Visitors with disabilities
A journalist
The Eiffel Tower on social media
Follow us on social networks
Facebook
X
Instagram
Competitions
Exclusive photos
All the news on the Eiffel Tower
Prices & Times
Access map
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



about:
website title: 
The Eiffel Tower: all there is to know - Official website
 and website content: 
Skip to main content
Prices & Times
Planning a smooth visit
Explore
Explore
The Esplanade
1st Floor
2nd Floor
The Top
The Gardens
The Tower
The Tower
In figures
The birth
Gustave Eiffel
The universal exhibition
Art
Paintings
The lifts
The lights
Science
History of the restaurants
Great towers of the world
English
EN
Français
English
Español
Italiano
Deutsch
Português
中文
日本語
عربي
Restaurants & gift shops
News
Search
Search
E-shop
Tickets
E-shop
Tickets
The Tower
History, key figures, lights, paintings, explore all the secrets of the world's most iconic monument
Eiffel tower facts, height & weight
An object of discord, desire and fascination, the Eiffel Tower never fails to impress. Enriched by a history full of new developments, here you can discover all of its key information.
Origins and Construction of the Eiffel Tower
It was for the
1889 Exposition Universelle
, the date that marked the 100th anniversary of the French Revolution, that a great competition was launched in 1886.
The first digging work started on the
26th January 1887
. On the 31st Marc...
Gustave Eiffel
The Tower is not Gustave Eiffel’s only creation. This enthusiast and true genius was able to go beyond his own limits to bequeath to us monuments such as the dome on the Nice Observatory, the metallic structure of the Statue of Liberty, not to mention the Bordeaux railway brid...
The Eiffel Tower during the 1889 Exposition Universelle
The tenth Exposition Universelle was organised in Paris in 1889, from the 15th May to the 6th November, and it was for this occasion that the Eiffel Tower was built. Stretching over 95 hectares, the Exposition filled the Champ-de-Mars, the Trocadero Hill, and the banks up to t...
Art and the Eiffel Tower
From the beginning the Tower was an attraction, but in the 1920s it became a symbol of modernity and the avant-garde. Little by little, its image was associated with Paris, until it even became its worldwide symbol.
Poets, painters, singers, choreographers, film dire...
The Eiffel Tower Laboratory
The Eiffel Tower was supposed to be destroyed only 20 years after its construction. To remedy the situation, Gustave Eiffel had the ingenious idea of crediting it with a scientific purpose – the Tower was saved!
The Eiffel Tower’s Lifts
Almost from the very opening of the Eiffel Tower for the 1889 Exposition Universelle, visitors could access the floors of the monument by taking the lifts. A veritable technical triumph for the time.
Painting the Eiffel Tower
The repainting campaign is an important event in the life of the monument and takes on a truly mythical nature, as with everything linked to the Eiffel Tower. It represents the lasting quality of a work of art known all over the world, the colour of the monument that is symbol...
History of the restaurants
For the Universal Exhibition of 1889, four majestic wooden pavilions designed by Stephen Sauvestre decked the platform on the first floor. Each restaurant could seat 500 people.
The Eiffel Tower in the world
« A vision, an object, a symbol, the Tower is anything that Man wants it to be, and this is infinite. A sight that is looked at and which looks back, a structure that is useless and yet irreplaceable, a familiar world and a heroic symbol, the witness to a century passing by an...
The Eiffel Tower’s Illuminations
Every evening, the Eiffel Tower is adorned with its golden covering and sparkles for 5 minutes every hour on the hour, while its beacon shines over Paris.
Prices & Times
Access map
Home
The Tower
Save time, buy your tickets online
Sur la billetterie officielle
Buy a ticket
toureiffel.paris the official website of the Eiffel Tower. A website owned by Sociéte d'Exploitation de la tour Eiffel
Access map
Contact
FAQ
Jobs
Press
Companies
Schools
Professionals in the Tourism Industry
SETE
Mairie de Paris
Legal information
Data protection policy
Cookies
Credits
Accessibility: partially compliant
Follow us on
Youtube
Facebook
Twitter
Linkedin
Instagram



contact:
website title: 
Guide visite
 and website content: 
Please enable JavaScript to continue using this application.



product:
website title: 
Paris Gift Ideas and Souvenirs - Official Eiffel Tower Shop
 and website content: 
Langues :
Fr
En
Es
The Eiffel Tower website
Contact us
Sign in
Cart
(0)
Gifts
The Paris Edit
Exceptional Gifts
The Iconics
For Her
For Him
For the children
Lifestyle
Decorative products
Tableware
Home Fragrance
Bookshop
Stationery
Gourmet
Leisure goods
Fashion
Clothes
Accessories
Shoes
Kids
Clothes & accessories
Bookshop
Games & toys
Bedroom & decoration
Collections
Limited Editions
Signature
Rainbow
Paris rooftops
The Olympic Collection
330 meters
Gustave Eiffel
Co-branding
Dammann Frères
Saint James
Bernardaud
La Sablésienne
Confiture Parisienne
OMY
Vilac
Kerzon
Payote
Pirouette Cacahouète
Search
Search
Search
No results found
An error occurred, please try again later
Home
The official Eiffel Tower shop
The Eiffel Tower Rivet
Last pieces available!
◆
Made in France
◆
Authentic Eiffel Tower steel
◆
Numbered item
Buy Now
Bernardaud
La Sablésienne
Saint James
OMY
Eiffel Tower style, from Paris to your home
An icon among icons
, the Eiffel Tower brings Parisian flair into your home through a
premium décor
collection where every detail celebrates
the French art of living
.
The Eiffel Tower Rivet -...
€525.00
White and Gold Bauble  -...
€16.99
Golden Glass Snow Globe -...
€14.99
Poster Restaurants -...
€59.00
New
Led Porcelain Lithophane...
€139.00
Eiffel Tower Bronze 35 cm -...
€49.00
Poster 30x40 - GUSTAVE...
€14.99
Vintage Snow Globe World's...
€16.99
See all products
The Eiffel Tower brand
date_range
22 July 2024
Discover the timeless excellence of the Tour Eiffel brand, where Gustave Eiffel's architectural heritage meets contemporary elegance. Each product, made in a limited edition in France, embodies the prestige and authenticity of a global icon.
Money back guarantee
Return within 14 days
Worldwide delivery
Express dispatch within 1-2 days
Payment in instalments
Payment information processed securely
Keep an eye on the Tower store
Discover our exclusive creations based on French know-how.
Your email
Need help?
Need help?
Returns and Refunds
Delivery
Guest order tracking
F.A.Q
Contact us
News & Events
News & Events
Limited Editions
The Olympic Collection
The Eiffel tower
The Eiffel tower
Tickets
Restaurants
Stores
SETE
Terms of use
Terms of use
Terms and Conditions of Sale
Terms of Use
Legal information
Privacy policy
Follow us
Follow us
Facebook
X
Instagram
Follow us
My wishlists
×
Create new list
((modalTitle))
×
((confirmMessage))
((cancelText))
((modalDeleteText))
((title))
×
((label))
((cancelText))
((createText))
Sign in
×
You need to be logged in to save products in your wishlist.
((cancelText))
((loginText))
Copyright
© 2025 Lagardère X Arteum
Retouched photographs
Langues :
Fr
En
Es



career:
website title: 
Careers at the Eiffel Tower | Official SETE website
 and website content: 
Skip to main content
SETE
Careers
Public procurement
Press area
E-shop
Eiffel Tower website
Careers
Every day, our 360 staff are hard at work running the Eiffel Tower and performing necessary maintenance, welcoming visitors from all over the world.
At SETE, some 360 staff bring their expertise and passion for the monument to work, serving the millions of visitors that the Eiffel Tower welcomes every year.
A wide range of professional roles are on offer within SETE, from welcoming visitors to operations and maintenance roles, not to mention a whole selection of roles in sales, finance, IT, legal, marketing, and communications.
As part of its new Delegated Public Service contract awarded by the Conseil de Paris, SETE’s primary concern is making the Eiffel Tower an even better place to visit by modernising the way visitors are welcomed and the services available to them, and boosting the Eiffel Tower’s international image.
“The City of Paris wants to make the Eiffel Tower an unassailable showcase for the quality of Paris’ visitor experience” (Paris City Hall press release, June 2017)
The Eiffel Tower is open year-round, from morning until late at night, and even on public holidays. There’s always something happening! The magic of this outstanding monument creates a unique atmosphere.
Our employees are all immensely proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.
Our
Welcome Agents
account for almost half of our total staff. Working for the
Operations
department, they welcome and direct visitors with professionalism and courtesy. As such, they are the Eiffel Tower’s ambassadors and help to make it an unforgettable experience.
Our
staff
in the
Technical department
carry out maintenance, construction work, and planning at the monument. Key to the smooth operation of the Tower, our technical roles cover a wide range of skills (engineering, architecture, electricity, plumbing, painting, joinery, locksmithing, etc.)
Our Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments, etc. are also well-represented within SETE, and keep the company running as it should
SETE has also teamed up with leading partners to manage restaurants and shops and cleaning and security at the monument, etc. In total, around 600 people work for the Eiffel Tower and its visitors.
An ambitious HR policy
SETE
encourages internal mobility
and career development for its staff. It has implemented a dynamic skill management programme and supports its employees so that it can offer them attractive opportunities for career advancement within the company.
As part of the roles defined by the new delegated public service contract, SETE has also put into place an
ambitious human resources management programme
to help the company meet its challenges and
recruit new talent.
A socially responsible employer
SETE strives to support its employees in an effort to adapt to changes and meet visitor expectations, promote safe working conditions, providing a quality workplace, and embodying the values of a socially responsible employee.
As such, we pay special attention to gender equality and diversity, notably through a constant effort to bring staff from different cultures together. Almost 32 nationalities work at SETE, and 40% of our employees are women.
Contact us
Do you have a question about our HR policy or would you like to apply spontaneously?
Contact us
Home
Careers
A website owned by Sociéte d'Exploitation de la tour Eiffel
Anglais
Français
Anglais
Español
Careers
Public procurement
SETE
Youtube
Facebook
Twitter
Linkedin
Instagram
Mairie de Paris
Contact
Terms & conditions
External policy for personal data protection
Cookies
Credits

Here is a humorous and entertaining brochure about the Eiffel Tower company in markdown format:

**🌍 Brochure for La Tour Eiffel**

**🗼 Welcome to the Icon of Paris**

The Eiffel Tower isn’t just an iron masterpiece – it’s a global celebrity! Standing tall since 1889, she’s seen more selfies than any other landmark in the world.

**💡 Fun Facts**

* Built for the World’s Fair (and wasn’t supposed to stay forever!) 
* Weighs over 10,000 tons, but still manages to look graceful.
* Has hosted dinners, fireworks, proposals, and even parachute jumps (don’t try this at home).

**🎟️ What We Offer**

* Tickets & Tours – Skip the line (because life’s too short).
* Restaurants & Shops – Enjoy a taste of Paris.
* Maintenance & Operations – Keeping the tower standing tall.

**💼 Careers at La Tour Eiffel**

We have 360 staff working hard every day to run the Eiffel Tower and welcome visitors from all over the world. Our employees are proud to work for the Eiffel Tower, serving its visitors, and possess an excellent team spirit.

**👥 Meet Our Teams**

* Welcome Agents – Almost half of our total staff!
* Technical department – Keeping the tower running smoothly.
* Sales, Finance, Marketing/Communications, IT, Legal, and Human Resources departments – Keeping the company running as it should.

**💼 Join Our Team!**

SETE encourages internal mobility and career development for its staff. We have an ambitious HR policy that promotes gender equality and diversity.

**📲 Contact Us**

Do you have a question about our HR policy or would you like to apply spontaneously? Contact us!

**Follow Us!**

* Facebook: @EiffelTower
* Twitter: @EiffelTower
* Instagram: @EiffelTower

**💕 Stay Connected!**

Get the latest news and updates from the Eiffel Tower on our social media channels.

I hope you enjoy this brochure! Let me know if you have any further requests.

In [ ]:

links = generate_LLM_link()   
ed = website("https://www.sharesansar.com/")
print(links.get_relevant_link(ed))

In [ ]:
print(ed.link)
print(type(ed.link))

['https://www.facebook.com/ShareSansar.com.np/', 'https://twitter.com/share_sansar', 'https://www.sharesansar.com/login', 'https://www.sharesansar.com/register', '/contactus', '/faq', '/write-for-us', 'https://www.sharesansar.com', '/', '#', '/news-page', '/announcement', '#', '/inflation', '/bullion', '/gdp-market-capitalization', '/gdp-nepse-index', '/weekly-deposit-lending', '/government-revenue-expenditure', '/capital-expenditure', '/remittance', '/bfis-deposit-lending', '/short-term-interest-rates', '/budget', '#', '/market', '/live-trading', '#', '/stock-heat-map/turnover', '/stock-heat-map/volume', '/today-share-price', '/floorsheet', '/agm-list', '/proposed-dividend', '/sectorwise-share-price', '/indices-sub-indices', '/datewise-indices', '/top-brokers', '/nepse-candlestick-chart', '/index-history-data', '#', '/ipo-result', '/category/ipo-fpo-news', '/category/share-allotment', '#', '/company-list', '/mutual-fund-navs', '/merged-companies', '/merger-acquisition', '/suspended-co